In [1]:
## 计算subsystem 1   keras resnet
import tensorflow as tf
from tensorflow.keras.layers import Dense
from tensorflow.keras import Model
from tensorflow.keras.backend import clear_session
import numpy as np
from matplotlib import pyplot as plt
import os
import tensorflow_probability as tfp
import scipy.io as scio

dataFile = "xdata"  
data = scio.loadmat(dataFile)
xdata = data['xdata']

dataFile = "ydata"  
data = scio.loadmat(dataFile)
ydata = data['ydata']

dataFile = "zdata"  
data = scio.loadmat(dataFile)
zdata = data['zdata']

dataFile = "Ldata"  
data = scio.loadmat(dataFile)
Ldata = data['Ldata']

dataFile = "iptdata"  
data = scio.loadmat(dataFile)
iptdata = data['iptdata']
#ydata=tf.reshape(ydata, [Nu, 1])

Nu=xdata.shape[1]
xdata=tf.reshape(xdata, [Nu])
ydata=tf.reshape(ydata, [Nu])
zdata=tf.reshape(zdata, [Nu])

ipt=tf.cast(iptdata, dtype=tf.int32)
ipt =tf.reduce_sum(ipt, axis=0)
L=tf.cast(Ldata, dtype=tf.int32)
L=tf.reduce_sum(L, axis=0)
iptnp=ipt.numpy()
print(iptnp)
L=L.numpy()
LS=800
Ls=2

I01=tf.argmax(L)
print(I01, iptnp[I01])
i=I01
u1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
v1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
print(u1_train,u2_train,u3_train)
u_train=tf.stack([u1_train,u2_train,u3_train],axis=1)
v_train=tf.stack([v1_train,v2_train,v3_train],axis=1)
u_train=tf.cast(u_train, dtype=tf.float32)
v_train=tf.cast(v_train, dtype=tf.float32)
print(u_train)
print(v_train)

class myModel(Model):
  def __init__(self):
    super(myModel,self).__init__()
    self.layer1=Dense(20, activation='relu')
    self.layer2=Dense(20, activation='relu')
    self.layer3=Dense(20, activation='relu')
    self.layer4=Dense(20, activation='relu')
    self.layer5=Dense(20, activation='relu')
    self.layer6=Dense(20, activation='relu')
    self.layer7=Dense(3, kernel_regularizer=tf.keras.regularizers.l2())
  
  def call(self, x):
    x1=self.layer1(x)
    x1=self.layer2(x1)
    x1=self.layer3(x1)
    x1=self.layer4(x1)
    x1=self.layer5(x1)
    x1=self.layer6(x1)
    y=self.layer7(x1)
    y=y+x
    return y

model1=myModel()

model1.compile(optimizer='adam', loss='mse')

model1.fit(u_train, v_train, batch_size=128, epochs=2000, validation_split=0.01, validation_freq=20)

model1.summary()


[  0 166 798   0 147 798   0 136 798   0 126 798   0 119 798   0 110 798
   0 109 798   0 105 798   0 104 798   0 100 798   0 155 798   0 136 798
   0 124 798   0 119 798   0 111 798   0 105 798   0 102 798   0  98 798
   0  98 798   0  96 798   0 146 798   0 132 798   0 117 798   0 111 798
   0 106 798   0 101 798   0  98 798   0  94 798   0  89 798   0  88 798
   0 136 798   0 123 798   0 115 798   0 106 798   0  99 798   0  95 798
   0  91 798   0  89 798   0  86 798   0  82 798   0 134 798   0 119 798
   0 108 798   0 101 798   0  94 798   0  90 798   0  87 798   0  83 798
   0  82 798   0  78 798   0 123 798   0 114 798   0 102 798   0  94 798
   0  90 798   0  84 798   0  82 798   0  78 798   0  76 798   0  75 798
   0 119 798   0 106 798   0  95 798   0  89 798   0  87 798   0  80 798
   0  77 798   0  77 798   0  71 798   0  71 798   0 115 798   0 100 798
   0  91 798   0  87 798   0  81 798   0  77 798   0  73 798   0  71 798
   0  69 798   0  68 798   0 110 798   0  97 798   

In [2]:
## 计算其他几段数据误差
LI0=0
for k in range(20):
    print(k,'---------------------------------------')
    Llen=L.size
    error=np.zeros([Llen])
    for i in range(Llen):
        x1=tf.cast(xdata[LS*(i//Ls)+iptnp[i+i//Ls]], dtype=tf.float32)
        x1=tf.reshape(x1,[1])
        x2=tf.cast(ydata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x2=tf.reshape(x2,[1])
        x3=tf.cast(zdata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x3=tf.reshape(x3,[1])
        u=tf.stack([x1,x2,x3],axis=1)
        y1=np.zeros([3,L[i]])
        u1=tf.reduce_sum(u,axis=0)
        y1[:,0]=u1.numpy()
        for j in range(L[i]-1):
            clear_session()
            v=model1.predict(u, verbose=0)
            v=tf.constant(v)
            u=v
            y1[:,j+1]=v.numpy()
        
        y1=tf.cast(y1, dtype=tf.float32)
        ytrue1=tf.cast(xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue2=tf.cast(ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue3=tf.cast(zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue=tf.stack([ytrue1,ytrue2,ytrue3],axis=0)
        y=(y1-ytrue).numpy()
        #print(i,y1,ytrue)
        error[i]=tf.reduce_mean(np.power(y[0,:],2)+np.power(y[1,:],2)+np.power(y[2,:],2),axis=0)
        print(i,error[i])
    
    print(error)
    
    
    I=np.where(error<1e-1)[0]
    LI=I.size
    print(I)
    if LI==LI0:
        break
    LI0=LI
    
    u1_train =np.zeros([0])
    u2_train =np.zeros([0])
    u3_train =np.zeros([0])
    v1_train =np.zeros([0])
    v2_train =np.zeros([0])
    v3_train =np.zeros([0])
    for i in I:
        u1_train=np.append(u1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u2_train=np.append(u2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u3_train=np.append(u3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        v1_train=np.append(v1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v2_train=np.append(v2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v3_train=np.append(v3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
    
    u_train=tf.stack([u1_train,u2_train,u3_train],axis=1)
    v_train=tf.stack([v1_train,v2_train,v3_train],axis=1)
    u_train=tf.cast(u_train, dtype=tf.float32)
    v_train=tf.cast(v_train, dtype=tf.float32)
    #print(u_train)
    #print(v_train)

#    model1=myModel()

#    model1.compile(optimizer='adam', loss='mse')

#checkpoint_save_path="./checkpoint/mnist.ckpt"
#if os.path.exists(checkpoint_save_path + '.index'):
#  print('-------------------load the model---------------------')
#  model1.load_weights(checkpoint_save_path)

#cp_callback=tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_save_path,
#                        save_weights_only=True,
#                        save_best_only=True)

#history=model1.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, callbacks=[cp_callback])

    model1.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, verbose=0)

#    model1.summary()

0 ---------------------------------------
0 2.202118396759033
1 2.1688127517700195
2 1.68973970413208
3 1.4965620040893555
4 1.438994288444519
5 1.0111647844314575
6 1.2272683382034302
7 0.7586826086044312
8 1.0878812074661255
9 0.5932042002677917
10 0.9336811304092407
11 0.41065704822540283
12 0.9064986705780029
13 0.25642770528793335
14 0.8251451253890991
15 0.19949252903461456
16 0.8040580749511719
17 0.13538266718387604
18 0.7421632409095764
19 0.07785561680793762
20 1.9145115613937378
21 1.6880511045455933
22 1.4603596925735474
23 1.3477668762207031
24 1.207755446434021
25 0.9444997310638428
26 1.0954046249389648
27 0.8173303008079529
28 0.9433342814445496
29 0.46971967816352844
30 0.8389564752578735
31 0.42806777358055115
32 0.7890694737434387
33 0.25926947593688965
34 0.6987784504890442
35 0.18946580588817596
36 0.6976839900016785
37 0.09104890376329422
38 0.6702601313591003
39 0.06126217544078827
40 1.692894458770752
41 1.9023946523666382
42 1.3696647882461548
43 1.367997884750

KeyboardInterrupt: 

In [5]:
## 计算subsystem 2   keras resnet
L1=L
L1=np.delete(L,I)
I02=tf.argmax(L1)
print(I02)

i=2*I02
u1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
v1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
#x_train =tf.reduce_sum(xdata, axis=0)
#y_train =tf.reduce_sum(ydata, axis=0)
u_train=tf.stack([u1_train,u2_train,u3_train],axis=1)
v_train=tf.stack([v1_train,v2_train,v3_train],axis=1)
u_train=tf.cast(u_train, dtype=tf.float32)
v_train=tf.cast(v_train, dtype=tf.float32)
print(iptnp)
print(u_train)
print(v_train)

class myModel2(Model):
  def __init__(self):
    super(myModel2,self).__init__()
    self.layer1=Dense(20, activation='relu')
    self.layer2=Dense(20, activation='relu')
    self.layer3=Dense(20, activation='relu')
    self.layer4=Dense(20, activation='relu')
    self.layer5=Dense(20, activation='relu')
    self.layer6=Dense(20, activation='relu')
    self.layer7=Dense(3, kernel_regularizer=tf.keras.regularizers.l2())
  
  def call(self, x):
    x1=self.layer1(x)
    x1=self.layer2(x1)
    x1=self.layer3(x1)
    x1=self.layer4(x1)
    x1=self.layer5(x1)
    x1=self.layer6(x1)
    y=self.layer7(x1)
    y=y+x
    return y

model2=myModel2()

model2.compile(optimizer='adam', loss='mse')

model2.fit(u_train, v_train, batch_size=128, epochs=2000, validation_split=0.01, validation_freq=20)

model2.summary()



tf.Tensor(0, shape=(), dtype=int64)
[  0 166 798   0 147 798   0 136 798   0 126 798   0 119 798   0 110 798
   0 109 798   0 105 798   0 104 798   0 100 798   0 155 798   0 136 798
   0 124 798   0 119 798   0 111 798   0 105 798   0 102 798   0  98 798
   0  98 798   0  96 798   0 146 798   0 132 798   0 117 798   0 111 798
   0 106 798   0 101 798   0  98 798   0  94 798   0  89 798   0  88 798
   0 136 798   0 123 798   0 115 798   0 106 798   0  99 798   0  95 798
   0  91 798   0  89 798   0  86 798   0  82 798   0 134 798   0 119 798
   0 108 798   0 101 798   0  94 798   0  90 798   0  87 798   0  83 798
   0  82 798   0  78 798   0 123 798   0 114 798   0 102 798   0  94 798
   0  90 798   0  84 798   0  82 798   0  78 798   0  76 798   0  75 798
   0 119 798   0 106 798   0  95 798   0  89 798   0  87 798   0  80 798
   0  77 798   0  77 798   0  71 798   0  71 798   0 115 798   0 100 798
   0  91 798   0  87 798   0  81 798   0  77 798   0  73 798   0  71 798
   0  69 798   

In [7]:
## 计算其他几段数据误差
LI0=0
for k in range(20):
    print(k,'---------------------------------------')
    Llen=L.size
    error=np.zeros([Llen])
    for i in range(Llen):
        x1=tf.cast(xdata[LS*(i//Ls)+iptnp[i+i//Ls]], dtype=tf.float32)
        x1=tf.reshape(x1,[1])
        x2=tf.cast(ydata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x2=tf.reshape(x2,[1])
        x3=tf.cast(zdata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x3=tf.reshape(x3,[1])
        u=tf.stack([x1,x2,x3],axis=1)
        y1=np.zeros([3,L[i]])
        u1=tf.reduce_sum(u,axis=0)
        y1[:,0]=u1.numpy()
        for j in range(L[i]-1):
            clear_session()
            v=model2.predict(u, verbose=0)
            v=tf.constant(v)
            u=v
            y1[:,j+1]=v.numpy()
        
        y1=tf.cast(y1, dtype=tf.float32)
        ytrue1=tf.cast(xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue2=tf.cast(ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue3=tf.cast(zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue=tf.stack([ytrue1,ytrue2,ytrue3],axis=0)
        y=(y1-ytrue).numpy()
        #print(i,y1,ytrue)
        error[i]=tf.reduce_mean(np.power(y[0,:],2)+np.power(y[1,:],2)+np.power(y[2,:],2),axis=0)
        print(i,error[i])
    
    print(error)
    
    
    I2=np.where(error<1e-1)[0]
    LI=I2.size
    print(I2)
    if LI==LI0:
        break
    LI0=LI
    
    u1_train =np.zeros([0])
    u2_train =np.zeros([0])
    u3_train =np.zeros([0])
    v1_train =np.zeros([0])
    v2_train =np.zeros([0])
    v3_train =np.zeros([0])
    for i in I2:
        u1_train=np.append(u1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u2_train=np.append(u2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u3_train=np.append(u3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        v1_train=np.append(v1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v2_train=np.append(v2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v3_train=np.append(v3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
    
    u_train=tf.stack([u1_train,u2_train,u3_train],axis=1)
    v_train=tf.stack([v1_train,v2_train,v3_train],axis=1)
    u_train=tf.cast(u_train, dtype=tf.float32)
    v_train=tf.cast(v_train, dtype=tf.float32)
    #print(u_train)
    #print(v_train)

#    model2=myModel2()

#    model2.compile(optimizer='adam', loss='mse')

#checkpoint_save_path="./checkpoint/mnist.ckpt"
#if os.path.exists(checkpoint_save_path + '.index'):
#  print('-------------------load the model---------------------')
#  model1.load_weights(checkpoint_save_path)

#cp_callback=tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_save_path,
#                        save_weights_only=True,
#                        save_best_only=True)

#history=model2.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, callbacks=[cp_callback])

    model2.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, verbose=0)

#    model2.summary()

0 ---------------------------------------
0 0.00028244536952115595
1 19.337390899658203
2 0.001961570465937257
3 19.792184829711914
4 0.005984930787235498
5 20.305482864379883
6 0.011318542994558811
7 20.932302474975586
8 0.01610204204916954
9 21.48154640197754
10 0.024054117500782013
11 22.20263671875
12 0.028433896601200104
13 22.75155258178711
14 0.03413843736052513
15 23.315292358398438
16 0.04101664200425148
17 23.925928115844727
18 0.04720815271139145
19 24.572126388549805
20 0.0003025803016498685
21 19.77301597595215
22 0.0031440947204828262
23 20.32054901123047
24 0.008161503821611404
25 20.8413028717041
26 0.01216946355998516
27 21.235525131225586
28 0.02042469196021557
29 22.023818969726562
30 0.025896696373820305
31 22.566007614135742
32 0.031184181571006775
33 23.192031860351562
34 0.03914138674736023
35 23.883909225463867
36 0.04319048300385475
37 24.488155364990234
38 0.04713110625743866
39 25.083189010620117
40 0.0003780238621402532
41 20.077836990356445
42 0.00250107562

In [8]:
## Inferring Transition Logic
x11 =np.zeros([0])
x12 =np.zeros([0])
x13 =np.zeros([0])
for i in I:
    x11=np.append(x11,xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x12=np.append(x12,ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x13=np.append(x13,zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    
L0=x11.shape[0]
J1=np.ones(L0)
J2=0*np.ones(L0)
x_train1=tf.stack([x11,x12,x13,J1,J2],axis=1)

x31 =np.zeros([0])
x32 =np.zeros([0])
x33 =np.zeros([0])
x41 =np.zeros([0])
x42 =np.zeros([0])
x43 =np.zeros([0])
for i in I2:
    x31=np.append(x31,xdata[(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x32=np.append(x32,ydata[(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x33=np.append(x33,zdata[(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x41=np.append(x41,xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x42=np.append(x42,ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x43=np.append(x43,zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    
L0=x31.shape[0]
J1=0*np.ones(L0)
J2=np.ones(L0)
x_train3=tf.stack([x31,x32,x33,J1,J2],axis=1)
L0=x41.shape[0]
J1=0*np.ones(L0)
J2=np.ones(L0)
x_train4=tf.stack([x41,x42,x43,J1,J2],axis=1)

x_train1=tf.cast(x_train1,dtype=tf.float32)
x_train3=tf.cast(x_train3,dtype=tf.float32)
x_train4=tf.cast(x_train4,dtype=tf.float32)
print(x_train1,x_train3,x_train4)
tf_optimizer = tf.keras.optimizers.Adam(learning_rate=0.002,beta_1=0.999,epsilon=1e-2)
#tf_optimizer = tf.keras.optimizers.Adam(learning_rate=0.1,beta_1=0.99,epsilon=1e-1)

class myModel_ITL():
  def __init__(self,optimizer,x_train1,x_train3,x_train4):
    self.u_model=tf.keras.Sequential()
    self.u_model.add(tf.keras.layers.InputLayer(input_shape=(5,)))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      2, activation=tf.nn.softmax,
      kernel_initializer='glorot_normal'))
        
    self.optimizer=optimizer
    self.dtype=tf.float32

  # Defining custom loss
  def __loss(self):
    y1NN=self.u_model(x_train1)
    y1=y1NN[:,0]
    y3NN=self.u_model(x_train3)
    y3=y3NN[:,0]
    y4NN=self.u_model(x_train4)
    y4=y4NN[:,1]
    return tf.reduce_mean(-tf.math.log(y1),axis=0)  + \
     tf.reduce_mean(-tf.math.log(y3),axis=0)  + \
     tf.reduce_mean(-tf.math.log(y4),axis=0)

  def __grad(self):
    with tf.GradientTape() as tape:
      loss_value = self.__loss()
    return loss_value, tape.gradient(loss_value, self.__wrap_training_variables())
    
  def __wrap_training_variables(self):
    var = self.u_model.trainable_variables
    return var
    
  def summary(self):
    return self.u_model.summary()

  # The training function
  def fit(self, tf_epochs=5000):
    # Creating the tensors
    #X_u = tf.convert_to_tensor(X_u, dtype=self.dtype)
    #u = tf.convert_to_tensor(u, dtype=self.dtype)
    #print(self.__wrap_training_variables())

    LOSS=np.zeros([1,tf_epochs])
    for epoch in range(tf_epochs):
      # Optimization step
      loss_value, grads = self.__grad()
      self.optimizer.apply_gradients(zip(grads, self.__wrap_training_variables()))
      LOSS[0,epoch]=loss_value.numpy()
      print('epoch, loss_value:', epoch, loss_value)

    scio.savemat('LOSS.mat',{'LOSS':LOSS})
    
  def predict(self, X_star):
    u_star = self.u_model(X_star)
    return u_star

    
model_ITL=myModel_ITL(tf_optimizer, x_train1, x_train3, x_train4)

model_ITL.fit(tf_epochs=100000)

model_ITL.summary()


tf.Tensor(
[[0.4063345  2.2841413  0.3499243  1.         0.        ]
 [0.41016608 2.2780066  0.34851953 1.         0.        ]
 [0.41414163 2.2718086  0.34783435 1.         0.        ]
 ...
 [3.8995104  0.60752827 1.0126126  1.         0.        ]
 [3.9019148  0.6051364  1.0113801  1.         0.        ]
 [3.9042988  0.60439134 1.0101949  1.         0.        ]], shape=(70077, 5), dtype=float32) tf.Tensor(
[[0.402118   2.2907972  0.35099053 0.         1.        ]
 [0.39944723 2.0610428  0.44987693 0.         1.        ]
 [0.4050553  1.9091657  0.5671247  0.         1.        ]
 [0.4050175  1.7852184  0.66844535 0.         1.        ]
 [0.40073618 1.7044456  0.7521914  0.         1.        ]
 [0.40006644 1.6021346  0.86943597 0.         1.        ]
 [0.40220127 1.5765172  0.9630677  0.         1.        ]
 [0.4010154  1.5153786  1.049043   0.         1.        ]
 [0.4032916  1.4929982  1.1516784  0.         1.        ]
 [0.40565342 1.4471949  1.2740577  0.         1.        ]
 [0.400185

In [13]:
## validation
x1=tf.constant([0], dtype=tf.float32)
x2=tf.constant([0.5], dtype=tf.float32)
x3=tf.constant([0.6283], dtype=tf.float32)
x4=tf.constant([0], dtype=tf.float32)
x5=tf.constant([1], dtype=tf.float32)
NT=799
X=x1
Y=x2
Z=x3
for i in range(NT):
    x=tf.stack([x1,x2,x3],axis=1)
    if x4>0.5:
        y=model1.predict(x, verbose=0)
    else:
        y=model2.predict(x, verbose=0)
    x_t=tf.stack([x1,x2,x3,x4,x5],axis=1)
    y_t=model_ITL.predict(x_t)
    
    X=np.append(X,y[0,0])
    Y=np.append(Y,y[0,1])
    Z=np.append(Z,y[0,2])
    x1=y[0,0]
    x1=tf.reshape(x1,[1])
    x2=y[0,1]
    x2=tf.reshape(x2,[1])
    x3=y[0,2]
    x3=tf.reshape(x3,[1])
    print(i,y,y_t,x4,x5)
    if y_t[0,0]>0.5:
        x4=tf.constant([1], dtype=tf.float32)
        x5=tf.constant([0], dtype=tf.float32)
    else:
        x4=tf.constant([0], dtype=tf.float32)
        x5=tf.constant([1], dtype=tf.float32)

scio.savemat('validationx.mat',{'X':X})
scio.savemat('validationy.mat',{'Y':Y})
scio.savemat('validationz.mat',{'Z':Z})
print(X,Y,Z)

0 [[0.00150384 0.5134097  0.6273452 ]] tf.Tensor([[0. 1.]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
1 [[0.00304745 0.52680767 0.62639666]] tf.Tensor([[0. 1.]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
2 [[0.00463079 0.540194   0.6254543 ]] tf.Tensor([[0. 1.]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
3 [[0.0062538  0.55356866 0.62451816]] tf.Tensor([[0. 1.]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
4 [[0.00791642 0.5669317  0.6235882 ]] tf.Tensor([[0. 1.]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
5 [[0.00961861 0.58028316 0.62266445]] tf.Tensor([[0. 1.]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=fl